# rf804_mcstudy_constr
Validation and MC studies: using RooMCStudy on models with constrains




**Author:** Wouter Verkerke  
<i><small>This notebook tutorial was automatically generated with <a href= "https://github.com/root-project/root/blob/master/documentation/doxygen/converttonotebook.py">ROOTBOOK-izer</a> from the macro found in the ROOT repository  on Monday, May 13, 2024 at 11:37 AM.</small></i>

In [1]:
%%cpp -d
#include "RooRealVar.h"
#include "RooDataSet.h"
#include "RooGaussian.h"
#include "RooPolynomial.h"
#include "RooAddPdf.h"
#include "RooProdPdf.h"
#include "RooMCStudy.h"
#include "RooPlot.h"
#include "TCanvas.h"
#include "TAxis.h"
#include "TH1.h"
using namespace RooFit;

Create model with parameter constraint
---------------------------------------------------------------------------

Observable

In [2]:
RooRealVar x("x", "x", -10, 10);

Signal component

In [3]:
RooRealVar m("m", "m", 0, -10, 10);
RooRealVar s("s", "s", 2, 0.1, 10);
RooGaussian g("g", "g", x, m, s);

Background component

In [4]:
RooPolynomial p("p", "p", x);

Composite model

In [5]:
RooRealVar f("f", "f", 0.4, 0., 1.);
RooAddPdf sum("sum", "sum", RooArgSet(g, p), f);

Construct constraint on parameter f

In [6]:
RooGaussian fconstraint("fconstraint", "fconstraint", f, 0.7, 0.1);

Multiply constraint with pdf

In [7]:
RooProdPdf sumc("sumc", "sum with constraint", RooArgSet(sum, fconstraint));

Setup toy study with model
---------------------------------------------------

Perform toy study with internal constraint on f

In [8]:
RooMCStudy mcs(sumc, x, Constrain(f), Silence(), Binned(), FitOptions(PrintLevel(-1)));

Run 500 toys of 2000 events.
Before each toy is generated, a value for the f is sampled from the constraint pdf and
that value is used for the generation of that toy.

In [9]:
mcs.generateAndFit(500, 2000);

[#0] PROGRESS:Generation -- RooMCStudy::run: sample 495
[#0] PROGRESS:Generation -- RooMCStudy::run: sample 490
[#0] PROGRESS:Generation -- RooMCStudy::run: sample 485
[#0] PROGRESS:Generation -- RooMCStudy::run: sample 480
[#0] PROGRESS:Generation -- RooMCStudy::run: sample 475
[#0] PROGRESS:Generation -- RooMCStudy::run: sample 470
[#0] PROGRESS:Generation -- RooMCStudy::run: sample 465
[#0] PROGRESS:Generation -- RooMCStudy::run: sample 460
[#0] PROGRESS:Generation -- RooMCStudy::run: sample 455
[#0] PROGRESS:Generation -- RooMCStudy::run: sample 450
[#0] PROGRESS:Generation -- RooMCStudy::run: sample 445
[#0] PROGRESS:Generation -- RooMCStudy::run: sample 440
[#0] PROGRESS:Generation -- RooMCStudy::run: sample 435
[#0] PROGRESS:Generation -- RooMCStudy::run: sample 430
[#0] PROGRESS:Generation -- RooMCStudy::run: sample 425
[#0] PROGRESS:Generation -- RooMCStudy::run: sample 420
[#0] PROGRESS:Generation -- RooMCStudy::run: sample 415
[#0] PROGRESS:Generation -- RooMCStudy::run: sam

Make plot of distribution of generated value of f parameter

In [10]:
TH1 *h_f_gen = mcs.fitParDataSet().createHistogram("f_gen", AutoBinning(40));

Make plot of distribution of fitted value of f parameter

In [11]:
RooPlot *frame1 = mcs.plotParam(f, Bins(40));
frame1->SetTitle("Distribution of fitted f values");

Make plot of pull distribution on f

In [12]:
RooPlot *frame2 = mcs.plotPull(f, Bins(40), FitGauss());
frame1->SetTitle("Distribution of f pull values");

TCanvas *c = new TCanvas("rf804_mcstudy_constr", "rf804_mcstudy_constr", 1200, 400);
c->Divide(3);
c->cd(1);
gPad->SetLeftMargin(0.15);
h_f_gen->GetYaxis()->SetTitleOffset(1.4);
h_f_gen->Draw();
c->cd(2);
gPad->SetLeftMargin(0.15);
frame1->GetYaxis()->SetTitleOffset(1.4);
frame1->Draw();
c->cd(3);
gPad->SetLeftMargin(0.15);
frame2->GetYaxis()->SetTitleOffset(1.4);
frame2->Draw();

[#1] INFO:ObjectHandling -- RooWorkspace::import() importing RooRealVar::fpull

[#1] INFO:Fitting -- RooAbsPdf::fitTo(pullGauss_over_pullGauss_Int[fpull]) fixing normalization set for coefficient determination to observables in data
[#1] INFO:Fitting -- using CPU computation library compiled with -mavx2
[#1] INFO:Fitting -- RooAddition::defaultErrorLevel(nll_pullGauss_over_pullGauss_Int[fpull]_fitParData_sumc) Summation contains a RooNLLVar, using its error level
[#1] INFO:Minimization -- RooAbsMinimizerFcn::setOptimizeConst: activating const optimization
[#1] INFO:Minimization -- RooAbsMinimizerFcn::setOptimizeConst: deactivating const optimization


Draw all canvases 

In [13]:
%jsroot on
gROOT->GetListOfCanvases()->Draw()